In [1]:
import torch
import numpy as np
from transformers import AutoModel, AutoTokenizer
from onnxruntime import InferenceSession

# PyTorch modeli yükle
model_name = "yazge/turkish-colbert-onnx"
tokenizer = AutoTokenizer.from_pretrained(model_name)
model = AutoModel.from_pretrained(model_name)

text = "Bu bir test cümlesidir."
inputs = tokenizer(text, return_tensors="pt")

# PyTorch modelinden çıktı al
with torch.no_grad():
    torch_out = model(**inputs).last_hidden_state.numpy()

# ONNX modelini yükle
session = InferenceSession("onnx/model.onnx")
onnx_inputs = {k: v.numpy() for k, v in inputs.items()}
onnx_out = session.run(None, onnx_inputs)[0]

# Maksimum farkı hesapla
max_diff = np.max(np.abs(torch_out - onnx_out))
print(f"PyTorch vs ONNX max diff: {max_diff}")


/home/ec2-user/miniconda3/envs/fastembed/lib/python3.10/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


PyTorch vs ONNX max diff: 8.58306884765625e-06
